# Table of Contents
 <p><div class="lev1"><a href="#Course-structure:-Climate-vs.-China300.1x"><span class="toc-item-num">1&nbsp;&nbsp;</span>Course structure: Climate vs. China300.1x</a></div><div class="lev2"><a href="#By-chapter"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>By chapter</a></div><div class="lev2"><a href="#By-order-of-course-items"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>By order of course items</a></div><div class="lev2"><a href="#Course-structure-vs.-students'-activity"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>Course structure vs. students' activity</a></div><div class="lev1"><a href="#Density-map-illustrating-pattern-of-video-and-problem-activity-for-the-involved"><span class="toc-item-num">2&nbsp;&nbsp;</span>Density map illustrating pattern of video and problem activity for the involved</a></div><div class="lev1"><a href="#Students-engagement:-multi_courses"><span class="toc-item-num">3&nbsp;&nbsp;</span>Students engagement: multi_courses</a></div><div class="lev2"><a href="#Bar-graph"><span class="toc-item-num">3.1&nbsp;&nbsp;</span>Bar graph</a></div><div class="lev2"><a href="#Heatmap"><span class="toc-item-num">3.2&nbsp;&nbsp;</span>Heatmap</a></div>

In [90]:
%matplotlib inline
from __future__ import division
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from collections import OrderedDict

import plotly
import plotly.offline as py
import plotly.graph_objs as go
import plotly.tools as tls

py.init_notebook_mode() # graphs charts inline (IPython).

## Course structure: Climate vs. China300.1x
### By chapter

In [91]:
def query_moduleActivity(course_id):
    """
    Give the course_id, query # students with any activity, # students attempted any problem 
    and # students watched any video for each chapter of the course
    """
    # query # students attempted any problem for each chapter of the course, exclude those with less than 20 attempts
    query = """
    Select course_id, sub.index As index, module_id, chapter_name, exact_count_distinct(user_id) As tried_problem
    From
    (SELECT p.course_id As course_id, p.user_id As user_id, c2.index As index, 
    c2.module_id As module_id, c2.name As chapter_name
    FROM [{0}.problem_analysis] p
    Left Join [{0}.course_axis] c1
    on p.problem_url_name = c1.url_name
    Left Join [{0}.course_axis] c2
    On c1.chapter_mid = c2.module_id) sub
    Group By course_id, index, module_id, chapter_name
    Order By index""".format(course_id)
    tried_problem = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False)
    tried_problem = tried_problem[tried_problem.tried_problem > 20]

    # query # students watched any video for each chapter of the course, exclude those with less than 20 views
    query = """
    Select course_id, index, module_id, chapter_name, exact_count_distinct(username) As watched_video
    From
    (SELECT c1.course_id As course_id, v.username As username, c2.index As index, 
    c2.module_id As module_id, c2.name As chapter_name
    FROM [{0}.video_stats_day] v
    Left Join [{0}.course_axis] c1
    on v.video_id = c1.url_name
    Left Join [{0}.course_axis] c2
    On c1.chapter_mid = c2.module_id) sub
    Group By course_id, index, module_id, chapter_name
    Order By index""".format(course_id)
    watched_video = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False)
    watched_video = watched_video[watched_video.watched_video > 20]

    # query # students with any activity for each chapter of the course, excluding those with less than 20 active students
    query = """
    Select sub.course_id As course_id, sub.module_id As module_id, 
    c.name As chapter_name, c.index As index, sub.nactive As nactive
    From [{0}.course_axis] c
    Join 
    (Select course_id As course_id, Regexp_replace(module_id,'i4x://', '') As module_id, 
    exact_count_distinct(student_id) As nactive
    From [{0}.studentmodule]
    Where module_type = 'chapter' 
    Group By course_id, module_id) sub
    On sub.module_id = c.module_id
    Order By index""".format(course_id)
    nactive = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False)
    nactive = nactive[nactive.nactive > 20]
    
    # merge watched_video, tried_problem, nactive 
    module_activity = watched_video.merge(tried_problem, how='outer').merge(nactive, how='outer').fillna(0)
    return module_activity[module_activity.chapter_name != 0].sort_values('index').set_index('chapter_name')
    
module_activity = query_moduleActivity('UBCx__Climate101x__3T2015')
# create a list of course indices to make sure courses are ordered in the visualization
indices = module_activity.index

In [92]:
def query_cs(course_id, indices):    
    """
    Given course_id (e.g. 'UBCx__Climate1x__1T2016'), 
    return a list of all the course items (graded_problem, self_test, video, assignment, chapter) 
    from course_axis table ordered by index.
    IMPORTANT: Need to update course_axis in SPD1x first (delete items that belong to SPD2x and SPD3x)
    """
    query = """
    SELECT
    Case 
         When c1.category='problem' And c1.graded='true' Then 'graded_problem'
         When c1.category='problem' And c1.graded!='true' Then 'self_test' 
         Else c1.category
    End As category, c1.index As index, c1.name As name,
    c1.url_name As url_name, c2.name As chapter
    FROM [[{0}.course_axis] c1
    Left Join [{0}.course_axis] c2
    On c1.chapter_mid = c2.module_id
    Where c1.category in ('video', 'problem', 'openassessment', 'chapter')
    Order By c1.index""".format(course_id)

    structure = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False)
    structure = structure[(structure.name.isin(indices)) | (structure.chapter.isin(indices))]
    
    query = """
    Select problem_url_name, exact_count_distinct(item.answer_id) As num
    From [{0}.problem_analysis]
    Group By problem_url_name""".format(course_id)
    nQuestions = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False)
    structure = structure.merge(nQuestions, left_on='url_name', right_on='problem_url_name', how='left')\
    .drop('problem_url_name', axis=1)
    structure.num = structure.num.fillna(1)
    return structure

course_structure = query_cs('UBCx__Climate101x__3T2015', indices)

In [93]:
# count # of videos, graded_problems, self_test and assigments for each chapter and order te courses
cs_chapter = course_structure.groupby(['chapter', 'category']).num.sum().unstack('category')\
.reindex(indices).dropna(how='all')

cols = []
# some courses don't have all the items
for col in ['video', 'graded_problem', 'self_test', 'openassessment']:
    if col in cs_chapter.columns.values:
        cols.append(col)
cs_chapter = cs_chapter[cols]
cs_chapter['chapter'] = np.nan
cs_chapter.fillna(0, inplace=True)

In [94]:
module_activity2 = query_moduleActivity('UBCx__China300_1x__1T2016')
# create a list of course indices to make sure courses are ordered in the visualization
indices2 = module_activity2.index
course_structure2 = query_cs('UBCx__China300_1x__1T2016', indices2)

In [95]:
# count # of videos, graded_problems, self_test and assigments for each chapter and order te courses
cs_chapter2 = course_structure2.groupby(['chapter', 'category']).num.sum().unstack('category')\
.reindex(indices2).dropna(how='all')

cols = []
# some courses don't have all the items
for col in ['video', 'graded_problem', 'self_test', 'openassessment']:
    if col in cs_chapter2.columns.values:
        cols.append(col)
cs_chapter2 = cs_chapter2[cols]
cs_chapter2['chapter'] = np.nan
cs_chapter2.fillna(0, inplace=True)

In [96]:
module_activity = module_activity.reindex(cs_chapter.index)
fig = tls.make_subplots(rows=1, cols=2, print_grid=False, 
                        subplot_titles=('UBCx/Climate101x/3T2015', 'UBCx/China300.1x/1T2016'))

colors = {'video': 'rgb(202,178,214)', 'graded_problem': 'rgb(66,146,198)', 
          'self_test': 'rgb(166,206,227)', 'openassessment': 'rgb(116,196,118)', 'chapter': 'rgb(0, 0, 0)'}

for i in range(0, cs_chapter.shape[1]):
    fig.append_trace(go.Bar(x=cs_chapter.index, y=cs_chapter.ix[:, i],
                       marker=dict(color=colors[cs_chapter.columns[i]]), name=cs_chapter.columns[i]), 1, 1)
    
for i in range(0, cs_chapter2.shape[1]):
    fig.append_trace(go.Bar(x=cs_chapter2.index, y=cs_chapter2.ix[:, i], 
                       marker=dict(color=colors[cs_chapter.columns[i]]), name=cs_chapter.columns[i], showlegend=False), 1, 2)

fig['layout']['yaxis1'].update(tickfont=dict(size=8), showgrid=False)
fig['layout']['yaxis2'].update(showticklabels=False, showgrid=False)
fig['layout']['xaxis1'].update(showgrid=False)
fig['layout']['xaxis2'].update(showgrid=False)
fig['layout']['legend'].update(x=1, y=0, traceorder='normal')
fig['layout'].update(height=380, width=850, margin=go.Margin(b=150, l=20, r=20, t=25), barmode='stack')
py.iplot(fig)

### By order of course items

In [97]:
def rolling_count(df):
    df['block'] = (df['category'] != df['category'].shift(1)).astype(int).cumsum()
    df['count'] = df.groupby('block').num.cumsum()
    return df
# count # of times an item (graded_problem, self_test, video) appears consecutively
df = course_structure.fillna(method='bfill')
df = df.groupby('chapter').apply(rolling_count)
idx = df.groupby(['chapter', 'block'])['count'].transform(max) == df['count']
df = df.ix[idx]

In [98]:
# plotting    
data = [go.Bar(x=df['count'], y=['UBCx/Climate101x/3T2015']*len(df), 
               orientation='h', hoverinfo='y',
              marker=dict(color=df.category.apply(lambda x: colors[x]).values))]
layout = go.Layout(
    xaxis=dict(tickfont=dict(size=8), showgrid=False),
#     yaxis=dict(showticklabels=False),
    barmode='stack', 
    width=850,
    height=50,
    margin=go.Margin(b=15, t=0, l=180)
)
fig = go.Figure(data=data, layout=layout)
py.iplot(fig)

In [99]:
df2 = course_structure2.fillna(method='bfill')
df2 = df2.groupby('chapter').apply(rolling_count)
idx2 = df2.groupby(['chapter', 'block'])['count'].transform(max) == df2['count']
df2 = df2.ix[idx2]

In [100]:
# plotting    
data = [go.Bar(x=df2['count'], y=['UBCx/China300.1x/1T2016']*len(df2), 
               orientation='h', hoverinfo='y',
              marker=dict(color=df2.category.apply(lambda x: colors[x]).values))]
layout = go.Layout(
    xaxis=dict(tickfont=dict(size=8), showgrid=False),
#     yaxis=dict(showticklabels=False),
    barmode='stack', 
    width=850,
    height=50,
    margin=go.Margin(b=15, t=0, l=180)
)
fig = go.Figure(data=data, layout=layout)
py.iplot(fig)

### Course structure vs. students' activity

In [101]:
def course_item(course_id):
    """
    Given course_id, query students' event for video, graded_problem, 
    self_test, openassessment and chapter from the studentmodule table
    => the numbers are slightly different from thosed queried from person_item and video_stats_day
    """
    query = """
    SELECT sub.module_id As item_id, c.index As index, name, category, nstudents
    FROM [ubcxdata:{0}.course_axis] c
    Join 
    (Select Regexp_replace(module_id,'i4x://', '') As module_id, exact_count_distinct(student_id) As nstudents
    From [ubcxdata:{0}.studentmodule]
    Where module_type In ('openassessment', 'chapter')
    Group By module_id) sub
    On sub.module_id = c.module_id
    Order By index""".format(course_id)
    chapter_assign = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False)

    query = """
    Select problem_url_name as item_id, index, name, 
    Case When graded='true' Then 'graded_problem' Else 'self_test' End As category,
    exact_count_distinct(user_id) As nstudents
    From [{0}.problem_analysis] p
    Join [{0}.course_axis] c
    On p.problem_url_name= c.url_name
    Group By item_id, index, name, category
    Order By index""".format(course_id)
    nproblems = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False)

    query = """
    Select video_id as item_id, index_video as index, name, 'video' As category, videos_viewed As nstudents
    From [{0}.video_stats]
    Where videos_viewed > 20""".format(course_id)
    nvideos = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False).dropna()

    courseItem = pd.concat([chapter_assign, nproblems, nvideos]).sort_values('index')
    courseItem = courseItem[courseItem.nstudents > 20].reset_index(drop=True)
    return courseItem

courseItem = course_item('UBCx__Climate101x__3T2015')

In [102]:
# make it center in the middle
trace1 = go.Bar(x=courseItem.index+1, y=courseItem.nstudents, hoverinfo='text',
               text=['{0}:<br>nstudents: {1}'.format(name.encode('utf-8'), value) 
                      for name, value in zip(courseItem.name, courseItem.nstudents)],
               marker=dict(color=courseItem.category.apply(lambda x: colors[x]).values))
trace2 = go.Bar(x=courseItem.index+1, y=-courseItem.nstudents, hoverinfo='none',
               marker=dict(color=courseItem.category.apply(lambda x: colors[x]).values))
data = [trace1, trace2]
layout = go.Layout(barmode='relative', title='UBCx/Climate101x/3T2015', 
                   xaxis=dict(showticklabels=False, title='course_structure'), 
                   yaxis=dict(showticklabels=False, showgrid=False, title='nstudents', zeroline=False), 
                   height=300, width=850, margin=go.Margin(t=25, b=15), showlegend=False)
fig = go.Figure(data=data, layout=layout)
py.iplot(fig)

In [103]:
courseItem2 = course_item('UBCx__China300_1x__1T2016')
# make it center in the middle
trace1 = go.Bar(x=courseItem2.index+1, y=courseItem2.nstudents, hoverinfo='text',
               text=['{0}:<br>nstudents: {1}'.format(name.encode('utf-8'), value) 
                      for name, value in zip(courseItem2.name, courseItem2.nstudents)],
               marker=dict(color=courseItem2.category.apply(lambda x: colors[x]).values))
trace2 = go.Bar(x=courseItem2.index+1, y=-courseItem2.nstudents, hoverinfo='none',
               marker=dict(color=courseItem2.category.apply(lambda x: colors[x]).values))
data = [trace1, trace2]
layout = go.Layout(barmode='relative', title='UBCx/China300.1x/1T2016', 
                   xaxis=dict(showticklabels=False, title='course_structure'), 
                   yaxis=dict(showticklabels=False, showgrid=False, title='nstudents', zeroline=False), 
                   height=300, width=850, margin=go.Margin(t=25, b=15), showlegend=False)
fig = go.Figure(data=data, layout=layout)
py.iplot(fig)

## Density map illustrating pattern of video and problem activity for the involved

In [104]:
def query_pc(course_id):     
    """
    Given course_id(e.g. 'UBCx__Marketing1x__3T2015'), query and calculate ndays_act, sum_dt, nforum_posts, 
    nvideos_watched, nproblems_attempted, pct_video_watched, pct_problem_attempted for sampled students,
    also return total_videos and total_problems.
    """
    query = """
    Select pc.user_id As user_id, pc.course_id As course_id, pc.mode As mode, pc.grade As grade, 
    pc.ndays_act As ndays_act, pc.sum_dt As sum_dt, pc.nforum_posts As nforum_posts,
    v.videos_watched As nvideos_watched, p.problems_attempted As nproblems_attempted
    From [{0}.person_course] pc
    Left Join
    (SELECT username, exact_count_distinct(video_id) As videos_watched 
    FROM [{0}.video_stats_day]
    Group By username) v
    on pc.username = v.username
    Left Join 
    (Select user_id, exact_count_distinct(item.answer_id) As problems_attempted
    From [{0}.problem_analysis]
    Group By user_id) p
    On pc.user_id = p.user_id
    Where pc.sum_dt > 0""".format(course_id)
    df = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False).fillna(0)

    # course_axis includes items not accessible to the students, 
    # => total_videos/total_problems are maximum number of videos/problems students accessed 
    # if smaller than the number from course_axis then use the latter one
    total_videos = min(df.nvideos_watched.max(), cs_chapter.video.sum())
    df['pct_video_watched'] = df.nvideos_watched / total_videos
    
    total_problems = min(df.nproblems_attempted.max(), 
                         cs_chapter.graded_problem.sum() + cs_chapter.self_test.sum() if 'self_test' in cs_chapter.columns 
                         else cs_chapter.graded_problem.sum())
    df['pct_problem_attempted'] = df.nproblems_attempted / total_problems
    
    
    return  total_videos, total_problems, df

In [105]:
total_videos, total_problems, pc = query_pc('UBCx__Climate101x__3T2015')
pc[['pct_video_watched', 'pct_problem_attempted']] = \
pc[['pct_video_watched', 'pct_problem_attempted']].applymap(lambda x: "{0:.2f}".format(x * 100))

In [106]:
# pc for the involved
pc_activity = pc[pc.sum_dt>900].copy()
# density map
trace1 = go.Histogram2d(x=pc_activity.pct_video_watched, y=pc_activity.pct_problem_attempted,
            histnorm='probability',
            autobinx=False,
            xbins=dict(start=0, end=100, size=10),
            autobiny=False,
            ybins=dict(start=0, end=100, size=10),
            colorscale=[[0, 'rgb(8,81,156)'], [1/1000, 'rgb(8,81,156)'], [1/100, 'rgb(242,211,56)'], 
                            [1/10, 'rgb(242,143,56)'], [1, 'rgb(217,30,30)']],
            showscale=False)
trace2 = go.Histogram2d(x=pc_activity.pct_video_watched, y=pc_activity.pct_problem_attempted,
            histnorm='probability',
            autobinx=False,
            xbins=dict(start=0, end=100, size=25),
            autobiny=False,
            ybins=dict(start=0, end=100, size=25),
            colorscale=[[0, 'rgb(8,81,156)'], [1/1000, 'rgb(8,81,156)'], [1/100, 'rgb(242,211,56)'], 
                            [1/10, 'rgb(242,143,56)'], [1, 'rgb(217,30,30)']],
            showscale=False)
trace3 = go.Histogram2d(x=pc_activity.pct_video_watched, y=pc_activity.pct_problem_attempted,
            histnorm='probability',
            autobinx=False,
            xbins=dict(start=0, end=100, size=10),
            autobiny=False,
            ybins=dict(start=0, end=100, size=10),
            colorscale=[[0, 'rgb(8,81,156)'], [1/1000, 'rgb(8,81,156)'], [1/100, 'rgb(242,211,56)'], 
                            [1/10, 'rgb(242,143,56)'], [1, 'rgb(217,30,30)']],
            colorbar=dict(thickness=20), zsmooth='fast')

fig = tls.make_subplots(rows=1, cols=3, print_grid=False)
fig.append_trace(trace1, 1, 1)
fig.append_trace(trace2, 1, 2)
fig.append_trace(trace3, 1, 3)

fig['layout']['xaxis1'].update(title='% videos (total:{0})'.format(int(total_videos)))
fig['layout']['xaxis2'].update(title='% videos (total:{0})'.format(int(total_videos)))
fig['layout']['xaxis3'].update(title='% videos (total:{0})'.format(int(total_videos)))
fig['layout']['yaxis1'].update(title='% problems (total:{0})'.format(int(total_problems)))
fig['layout']['yaxis2'].update(showticklabels=False)
fig['layout']['yaxis3'].update(showticklabels=False)
fig['layout'].update(
    width=850, height=350, 
    title='UBCx/Climate101x/3T2015',
    margin=go.Margin(l=40, t=40)
)
py.iplot(fig)

## Students engagement: multi_courses
### Bar graph

In [107]:
# only change course_list (for all courses on edX), mooc_list (Moocs) and pe_list (professional education) if needed
# list for all the courses
course_list = [
    'UBCx__Marketing1x__3T2015',
    'UBCx__Climate1x__2T2016',        
    'UBCx__SPD1x__2T2016',
    'UBCx__SPD2x__2T2016',
    'UBCx__SPD3x__2T2016',
    'UBCx__UseGen_1x__1T2016',
    'UBCx__UseGen_2x__1T2016',
    'UBCx__China300_1x__1T2016',
    'UBCx__China300_2x__1T2016',
    'UBCx__Forest222x__1T2015',
    'UBCx__IndEdu200x__3T2015',
    'UBCx__Water201x_2__2T2015',
    'UBCx__CW1_1x__1T2016',
    'UBCx__CW1_2x__1T2016',
    'UBCx__Phot1x__1T2016',
    'UBCx__ITSx__2T2015'
]
indices = [course.replace('__', '/').replace('_', '.') for course in course_list]
indices[indices.index('UBCx/Water201x.2/2T2015')] = 'UBCx/Water201x_2/2T2015'

In [108]:
# dictionaries to store total # of videos/problems for each course in the course_list
total_videos = {}
total_problems = {}
def query_pcs_learned(course_list = course_list):
    """
    Iterate over each course in the course_list, query and calculate ndays_act, sum_dt, nforum_posts, 
    nvideos_watched, nproblems_attempted, pct_video_watched, pct_problem_attempted for involved students.
    Update total_videos and total_problems
    """
    dfs = []
    for i in range(len(course_list)):
        query = """
        Select pc.user_id As user_id, pc.course_id As course_id, pc.mode As mode, pc.grade As grade, 
        pc.ndays_act As ndays_act, pc.sum_dt / 3600 As sum_dt, pc.nforum_posts As nforum_posts,
        v.videos_watched As nvideos_watched, p.problems_attempted As nproblems_attempted
        From [{0}.person_course] pc
        Left Join
        (SELECT username, Count(Distinct video_id) As videos_watched 
        FROM [{0}.video_stats_day]
        Group By username) v
        on pc.username = v.username
        Left Join 
        (Select user_id, Count(Distinct item.answer_id) As problems_attempted
        From [{0}.problem_analysis]
        Group By user_id) p
        On pc.user_id = p.user_id
        Where pc.sum_dt > 900""".format(course_list[i])
        df = pd.io.gbq.read_gbq(query, project_id='ubcxdata', verbose=False).fillna(0)

        course_id = indices[i]
        total_videos[course_id] = df.nvideos_watched.quantile(0.975)
        df['pct_video_watched'] = df.nvideos_watched / total_videos[course_id]
        total_problems[course_id] = df.nproblems_attempted.quantile(0.975)
        df['pct_problem_attempted'] = df.nproblems_attempted / total_problems[course_id]
        dfs.append(df)
    pcs_learned = pd.concat(dfs)
    return pcs_learned

In [109]:
cols = ['ndays_act', 'sum_dt', 'pct_video_watched', 'pct_problem_attempted', 'nforum_posts']
# for the involved
pcs_learned = query_pcs_learned()
# aggregate nforum_posts => % students posted, others by median
pcs_learned_agg = pcs_learned.groupby('course_id').agg({'ndays_act': np.median, 'sum_dt': np.median, 
                                                        'pct_video_watched': np.median, 'pct_problem_attempted': np.median, 
                                                        'nforum_posts': lambda s: (s > 0).sum() / len(s)})
# order the courses as needed
pcs_learned_agg = pcs_learned_agg[cols].reindex(indices)
# for the passed
pcs_passed = pcs_learned[pcs_learned.grade >= 0.5]
pcs_passed_agg = pcs_passed.groupby('course_id').agg({'ndays_act': np.median, 'sum_dt': np.median, 
                                                        'pct_video_watched': np.median, 'pct_problem_attempted': np.median, 
                                                        'nforum_posts': lambda s: (s > 0).sum() / len(s)})
pcs_passed_agg = pcs_passed_agg[cols].reindex(indices)

# normalize along the columns for plotting heatmap
pcs_passed_norm = pcs_passed_agg.divide(pcs_passed_agg.max(axis=0), axis=1)
pcs_learned_norm = pcs_learned_agg.divide(pcs_learned_agg.max(axis=0), axis=1)
# formatting
pcs_passed_agg.sum_dt = pcs_passed_agg.sum_dt.round(2)
pcs_passed_agg[['pct_video_watched', 'pct_problem_attempted', 'nforum_posts']] = \
pcs_passed_agg[['pct_video_watched', 'pct_problem_attempted', 'nforum_posts']].applymap(lambda x: "{0:.2f}".format(x * 100))
pcs_learned_agg.sum_dt = pcs_learned_agg.sum_dt.round(2)
pcs_learned_agg[['pct_video_watched', 'pct_problem_attempted', 'nforum_posts']] = \
pcs_learned_agg[['pct_video_watched', 'pct_problem_attempted', 'nforum_posts']].applymap(lambda x: "{0:.2f}".format(x * 100))

In [115]:
color_passed = ['rgb(166,206,227)', 'rgb(253,191,111)', 'rgb(178,223,138)', 'rgb(251,154,153)', 'rgb(202,178,214)']
color_learned = ['rgb(31,120,180)', 'rgb(255,127,0)', 'rgb(51,160,44)', 'rgb(227,26,28)', 'rgb(106,61,154)']
fig = tls.make_subplots(rows=1, cols=pcs_passed_agg.shape[1], horizontal_spacing=0.02, print_grid=False)
for i in range(0, pcs_passed_agg.shape[1]):
    fig.append_trace(go.Bar(x=pcs_passed_agg.ix[:, i], y=pcs_passed_agg.index, marker=dict(color=color_passed[i]),
                    name='passed', orientation='h', showlegend=False), 1, i+1)
    fig.append_trace(go.Bar(x=pcs_learned_agg.ix[:, i], y=pcs_learned_agg.index, marker=dict(color=color_learned[i]),
                            name='learned', orientation='h', showlegend=False), 1, i+1)

showticklabels = True
# fig['layout']['yaxis1'].update(autorange='reversed')
for i in range(1, pcs_passed_agg.shape[1]+1):
    if i >= 2:
        showticklabels = False
    fig['layout']['xaxis%s' % i].update(title=names[i-1], titlefont=dict(size=10), 
                                        tickfont=dict(size=8), showgrid=False)
    fig['layout']['yaxis%s' % i].update(showticklabels=showticklabels, showgrid=False, autorange='reversed')

fig['layout'].update(barmode='overlay', height=80+25*len(pcs_learned_agg),
                     width=800, margin=go.Margin(t=40, b=40, l=180, r=0), title="Engagement for the learned and the passed")
py.iplot(fig)

### Heatmap

In [111]:
# normalized value for plotting heatmap, unnormalized for hoverinfo
names = ['median days active', 'median sum_dt (H)', 
         'median % videos', 'median % problems', '% students posted']
trace1 = go.Heatmap(
            z=pcs_learned_norm.values,
            x=names,
            y=pcs_learned_norm.index,
            text = pcs_learned_agg.values,
            hoverinfo='x+text',
            showscale=False,
            colorscale=[[0.0, 'rgb(224,243,248)'], [1.0, 'rgb(51,160,44)']])


trace2 = go.Heatmap(
            z=pcs_passed_norm.values,
            x=names,
            y=pcs_passed_norm.index,
            text = pcs_passed_agg.values,
            hoverinfo='x+text',
            showscale=False,
            colorscale=[[0.0, 'rgb(224,243,248)'], [1.0, 'rgb(43,130,189)']])

fig = tls.make_subplots(rows=1, cols=2, print_grid=False,
                              subplot_titles=('Engagement for the involved', 
                                              'Engagement for the passed'))
fig.append_trace(trace1, 1, 1)
fig.append_trace(trace2, 1, 2)
fig['layout']['yaxis1'].update(autorange='reversed')
fig['layout']['yaxis2'].update(showticklabels=False, autorange='reversed')

fig['layout'].update(
    width=750, height=140+30*len(pcs_learned_agg),
    margin=go.Margin(l=180, b=120, t=20)
)

py.iplot(fig)